# Resave STORM6 raw data into MERlin format

* Data from: \\10.245.74.158\Chromatin_NAS_0\20220304-P_brain_M1_nonclear_adaptors

In [1]:
import os,glob,sys,time
import shutil
import numpy as np
sys.path.append(r"E:\Users\puzheng\Documents")
import ImageAnalysis3 as ia3

In [2]:
data_folder = r'\\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear'

fds, fovs = ia3.get_img_info.get_folders(data_folder)

Get Folder Names: (ia.get_img_info.get_folders)
- Number of folders: 12
- Number of field of views: 0


In [7]:
fov_names = [_fl.split(os.extsep)[0] for _fl in os.listdir(fds[0]) if '.dax' in _fl]

In [9]:
merfish_data_folder = r'I:\MERFISH_Data'
target_folder = os.path.join(merfish_data_folder, os.path.basename(data_folder)+'_renamed')
#target_folder = r'\20220226-P_brain_M1_nonclear'
if not os.path.isdir(target_folder):
    print(f"creating folder: {target_folder}")
    os.makedirs(target_folder)
ref_image_type = 'Epi-750-647-488-405-s50'
image_type = 'Epi-750-647-488-s13'

creating folder: I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed


In [11]:
import blosc

In [28]:
%%time

fov_ids = np.arange(len(fovs))
ref_round = 0

overwrite = False
remove_source=False

# loop through fovs
for _fov_id in fov_ids:
    # files
    for _fd in fds[:]:
        _files = [os.path.join(_fd, _fl) for _fl in os.listdir(_fd) if fov_names[_fov_id] in _fl and '.npy' not in _fl]
        # determine imaging protocol for this round
        _round = int(os.path.basename(_fd).split('H')[1].split('M')[0])
        if _round == ref_round:
            _image_type = ref_image_type
        else:
            _image_type = image_type
        # if its a dax.zst file, decompress
        for _fl in _files:
            # target file
            _tar_fl = os.path.join(target_folder, f"{_image_type}_{_fov_id}_{_round}{os.extsep}{os.path.basename(_fl).split(os.extsep)[1]}")
            if not os.path.isfile(_tar_fl) or overwrite:
                if 'dax.zst' in _fl:
                    print(f"decompress {_fl} to {_tar_fl}")
                    with open(_fl, 'rb') as _f:
                        _cp_image = _f.read()
                    _image = blosc.decompress(_cp_image)
                    _image_array = np.frombuffer(_image, dtype=np.uint16)
                    _image_array = _image_array.reshape([-1,2048,2048])
                    _image_array.tofile(_tar_fl)
                    if remove_source:
                        os.remove(_fl)
                else:
                    if remove_source:
                        print(f"move {_fl} to {_tar_fl}")
                        shutil.move(_fl, _tar_fl)
                    else:
                        print(f"copy {_fl} to {_tar_fl}")
                        shutil.copyfile(_fl, _tar_fl)
            else:
                print(f"{_tar_fl} already exist, skip")
    

I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-405-s50_0_0.dax already exist, skip
I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-405-s50_0_0.inf already exist, skip
I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-405-s50_0_0.off already exist, skip
I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-405-s50_0_0.power already exist, skip
I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-405-s50_0_0.xml already exist, skip
I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_0_1.dax already exist, skip
I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_0_1.inf already exist, skip
I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_0_1.off already exist, skip
I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_0_1.power already exist, skip
I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_0_1.

copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H3M4\Conv_zscan_001.inf to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_1_3.inf
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H3M4\Conv_zscan_001.off to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_1_3.off
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H3M4\Conv_zscan_001.power to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_1_3.power
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H3M4\Conv_zscan_001.xml to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_1_3.xml
decompress \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H4M5\Conv_zscan_001.dax.zst to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_1_4.dax
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H4M5\Conv_zscan_001.inf to I:\MERFISH_Data\20220409-P_brain_M

copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H1M2\Conv_zscan_002.inf to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_2_1.inf
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H1M2\Conv_zscan_002.off to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_2_1.off
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H1M2\Conv_zscan_002.power to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_2_1.power
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H1M2\Conv_zscan_002.xml to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_2_1.xml
decompress \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H2M3\Conv_zscan_002.dax.zst to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_2_2.dax
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H2M3\Conv_zscan_002.inf to I:\MERFISH_Data\20220409-P_brain_M

copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H11M12\Conv_zscan_002.inf to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_2_11.inf
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H11M12\Conv_zscan_002.off to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_2_11.off
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H11M12\Conv_zscan_002.power to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_2_11.power
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H11M12\Conv_zscan_002.xml to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_2_11.xml
decompress \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H0M1\Conv_zscan_003.dax.zst to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-405-s50_3_0.dax
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H0M1\Conv_zscan_003.inf to I:\MERFISH_Data\20

copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H9M10\Conv_zscan_003.inf to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_3_9.inf
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H9M10\Conv_zscan_003.off to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_3_9.off
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H9M10\Conv_zscan_003.power to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_3_9.power
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H9M10\Conv_zscan_003.xml to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_3_9.xml
decompress \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H10M11\Conv_zscan_003.dax.zst to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_3_10.dax
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H10M11\Conv_zscan_003.inf to I:\MERFISH_Data\20220409-

...

copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H3M4\Conv_zscan_186.power to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_186_3.power
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H3M4\Conv_zscan_186.xml to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_186_3.xml
decompress \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H4M5\Conv_zscan_186.dax.zst to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_186_4.dax
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H4M5\Conv_zscan_186.inf to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_186_4.inf
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H4M5\Conv_zscan_186.off to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_186_4.off
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H4M5\Conv_zscan_186.power to I:\MERFISH_Data\202204

decompress \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H1M2\Conv_zscan_187.dax.zst to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_187_1.dax
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H1M2\Conv_zscan_187.inf to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_187_1.inf
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H1M2\Conv_zscan_187.off to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_187_1.off
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H1M2\Conv_zscan_187.power to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_187_1.power
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H1M2\Conv_zscan_187.xml to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_187_1.xml
decompress \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H2M3\Conv_zscan_187.dax.zst to I:\MERFISH_Dat

copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H11M12\Conv_zscan_187.inf to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_187_11.inf
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H11M12\Conv_zscan_187.off to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_187_11.off
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H11M12\Conv_zscan_187.power to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_187_11.power
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H11M12\Conv_zscan_187.xml to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_187_11.xml
decompress \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H0M1\Conv_zscan_188.dax.zst to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-405-s50_188_0.dax
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H0M1\Conv_zscan_188.inf to I:\MERFI

copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H9M10\Conv_zscan_188.inf to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_188_9.inf
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H9M10\Conv_zscan_188.off to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_188_9.off
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H9M10\Conv_zscan_188.power to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_188_9.power
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H9M10\Conv_zscan_188.xml to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_188_9.xml
decompress \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H10M11\Conv_zscan_188.dax.zst to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_188_10.dax
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H10M11\Conv_zscan_188.inf to I:\MERFISH_Data

copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H7M8\Conv_zscan_189.inf to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_189_7.inf
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H7M8\Conv_zscan_189.off to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_189_7.off
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H7M8\Conv_zscan_189.power to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_189_7.power
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H7M8\Conv_zscan_189.xml to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_189_7.xml
decompress \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H8M9\Conv_zscan_189.dax.zst to I:\MERFISH_Data\20220409-P_brain_M1_noclear_renamed\Epi-750-647-488-s13_189_8.dax
copy \\10.245.74.158\Chromatin_NAS_0\20220409-P_brain_M1_noclear\H8M9\Conv_zscan_189.inf to I:\MERFISH_Data\20220409

In [21]:
_tar_fl

'I:\\MERFISH_Data\\20220409-P_brain_M1_noclear_renamed\\Epi-750-647-488-405-s50_0_0.dax'

In [24]:
_fl

'\\\\10.245.74.158\\Chromatin_NAS_0\\20220409-P_brain_M1_noclear\\H0M1\\Conv_zscan_000.dax.zst'

In [4]:
fov_ids = np.arange(len(fovs))

ref_round = 0
#fov_ids = np.arange(2)
overwrite = False
remove_source=False
# loop through fovs
for _fov_id in fov_ids:
    # files
    for _fd in fds[:]:
        _files = [os.path.join(_fd, _fl) for _fl in os.listdir(_fd) if fovs[_fov_id].split(os.extsep)[0] in _fl]
        _round = int(os.path.basename(_fd).split('H')[1].split('M')[0])
        if _round == ref_round:
            _image_type = ref_image_type
        else:
            _image_type = image_type
        # target file
        _target_files = [os.path.join(target_folder, f"{_image_type}_{_fov_id}_{_round}{os.extsep}{_fl.split(os.extsep)[-1]}") 
                         for _fl in _files]
        for _fl, _tar_fl in zip(_files, _target_files):
            if remove_source:
                print(f"move {_fl} to {_tar_fl}")
                shutil.move(_fl, _tar_fl)
            else:
                if not os.path.isfile(_tar_fl) or overwrite:
                    print(f"copy {_fl} to {_tar_fl}")
                    shutil.copyfile(_fl, _tar_fl)
                else:
                    print(f"{_tar_fl} already exist, skip")

copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H0M1\Conv_zscan_000.off to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-405-s50_0_0.off
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H0M1\Conv_zscan_000.dax to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-405-s50_0_0.dax
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H0M1\Conv_zscan_000.xml to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-405-s50_0_0.xml
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H0M1\Conv_zscan_000.power to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-405-s50_0_0.power
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H0M1\Conv_zscan_000.inf to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-405-s50_0_0.inf
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1

copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H9M10\Conv_zscan_000.xml to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_0_9.xml
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H9M10\Conv_zscan_000.dax to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_0_9.dax
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H10M11\Conv_zscan_000.off to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_0_10.off
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H10M11\Conv_zscan_000.inf to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_0_10.inf
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H10M11\Conv_zscan_000.power to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_0_10.power
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear

copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H6M7\Conv_zscan_001.off to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_1_6.off
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H7M8\Conv_zscan_001.inf to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_1_7.inf
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H7M8\Conv_zscan_001.xml to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_1_7.xml
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H7M8\Conv_zscan_001.off to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_1_7.off
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H7M8\Conv_zscan_001.dax to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_1_7.dax
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H7M8\

copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H5M6\Conv_zscan_002.dax to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_2_5.dax
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H5M6\Conv_zscan_002.off to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_2_5.off
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H5M6\Conv_zscan_002.inf to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_2_5.inf
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H5M6\Conv_zscan_002.xml to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_2_5.xml
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H5M6\Conv_zscan_002.power to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_2_5.power
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H

copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H2M3\Conv_zscan_003.power to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_3_2.power
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H3M4\Conv_zscan_003.dax to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_3_3.dax
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H3M4\Conv_zscan_003.power to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_3_3.power
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H3M4\Conv_zscan_003.inf to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_3_3.inf
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H3M4\Conv_zscan_003.xml to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_3_3.xml
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adapto

...

copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H6M7\Conv_zscan_193.off to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_193_6.off
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H6M7\Conv_zscan_193.power to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_193_6.power
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H6M7\Conv_zscan_193.xml to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_193_6.xml
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H6M7\Conv_zscan_193.inf to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_193_6.inf
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H7M8\Conv_zscan_193.inf to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_193_7.inf
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_

copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H3M4\Conv_zscan_194.xml to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_194_3.xml
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H3M4\Conv_zscan_194.inf to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_194_3.inf
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H4M5\Conv_zscan_194.power to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_194_4.power
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H4M5\Conv_zscan_194.xml to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_194_4.xml
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H4M5\Conv_zscan_194.dax to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_194_4.dax
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_

copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H0M1\Conv_zscan_195.power to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-405-s50_195_0.power
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H0M1\Conv_zscan_195.inf to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-405-s50_195_0.inf
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H1M2\Conv_zscan_195.dax to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_195_1.dax
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H1M2\Conv_zscan_195.inf to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_195_1.inf
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H1M2\Conv_zscan_195.off to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_195_1.off
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_n

copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H10M11\Conv_zscan_195.dax to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_195_10.dax
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H10M11\Conv_zscan_195.off to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_195_10.off
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H10M11\Conv_zscan_195.power to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_195_10.power
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H10M11\Conv_zscan_195.xml to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_195_10.xml
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H10M11\Conv_zscan_195.inf to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_195_10.inf
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_bra

copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H7M8\Conv_zscan_196.off to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_196_7.off
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H7M8\Conv_zscan_196.inf to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_196_7.inf
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H8M9\Conv_zscan_196.off to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_196_8.off
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H8M9\Conv_zscan_196.dax to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_196_8.dax
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_adaptors\H8M9\Conv_zscan_196.power to I:\MERFISH_Data\20220328-P_brain_M1_nonclear_adaptors\Epi-750-647-488-s13_196_8.power
copy \\10.245.74.158\Chromatin_NAS_0\20220328-P_brain_M1_nonclear_

# Copy parameter files

In [6]:
source_position_file = os.path.join(data_folder, 'Experiments', 'positions_all.txt')

parameter_home = r'E:\Users\puzheng\Documents\Merfish_analysis\Merfish_Analysis_Scripts\merlin_parameters'
target_position_file = os.path.join(parameter_home, 'positions',
                                    '20220328_positions.txt')
shutil.copyfile(source_position_file, target_position_file)

'E:\\Users\\puzheng\\Documents\\Merfish_analysis\\Merfish_Analysis_Scripts\\merlin_parameters\\positions\\20220328_positions.txt'

In [11]:
import re

In [12]:
file_result = re.search(r'(?P<imageType>[\w|-]+)_(?P<fov>[0-9]+)_(?P<imagingRound>[0-9]+)', _target_files[0])

In [13]:
file_result.group('imageType')

'Epi-750-647-561-s13'

In [9]:
print(str(list(np.arange(3,200,16))).replace(',',''))

[3 19 35 51 67 83 99 115 131 147 163 179 195]


In [10]:
(33/3-1)*4*4

160.0